In [4]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from datetime import datetime

# Load and prepare data
def load_data():
    # Load VIX data
    vix_url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"
    vix_df = pd.read_csv(vix_url)
    vix_df['DATE'] = pd.to_datetime(vix_df['DATE'])
    vix_df = vix_df.rename(columns={'DATE': 'Date', 'CLOSE': 'VIX'})
    
    # Load S&P 500 data
    sp500_url = "https://raw.githubusercontent.com/datasets/s-and-p-500/master/data/data.csv"
    sp500_df = pd.read_csv(sp500_url)
    sp500_df['Date'] = pd.to_datetime(sp500_df['Date'])
    
    # Merge datasets
    merged_df = pd.merge(sp500_df[['Date', 'SP500']], 
                        vix_df[['Date', 'VIX']], 
                        on='Date', 
                        how='inner')
    
    merged_df = merged_df.sort_values('Date')
    
    print(f"Data range: {merged_df['Date'].min()} to {merged_df['Date'].max()}")
    print(f"Total data points: {len(merged_df)}")
    
    return merged_df

def create_enhanced_visualization(df):
    # Create figure with secondary y-axis
    fig = make_subplots(specs=[[{"secondary_y": True}]])
    
    # Add S&P 500 trace with log scale
    fig.add_trace(
        go.Scatter(
            x=df['Date'],
            y=df['SP500'],
            name="S&P 500",
            line=dict(color='#4299e1', width=2)
        ),
        secondary_y=False
    )

    # Add VIX trace
    fig.add_trace(
        go.Scatter(
            x=df['Date'],
            y=df['VIX'],
            name="VIX",
            line=dict(color='#fc8181', width=2)
        ),
        secondary_y=True
    )

    # Define major market events
    market_events = [
        dict(x='2008-09-15', y=df['SP500'].max(), 
             text='2008 Financial Crisis<br>Lehman Brothers Bankruptcy',
             showarrow=True, arrowhead=2,
             arrowsize=1, arrowwidth=2,
             arrowcolor='#FF4136',
             ax=0, ay=-40),
        
        dict(x='2009-03-09', y=df['SP500'].max() * 0.8,
             text='2009 Market Bottom<br>S&P 500 hits 666',
             showarrow=True, arrowhead=2,
             arrowsize=1, arrowwidth=2,
             arrowcolor='#2ECC40',
             ax=50, ay=0),
        
        dict(x='2010-05-06', y=df['SP500'].max() * 0.85,
             text='Flash Crash',
             showarrow=True, arrowhead=2,
             arrowsize=1, arrowwidth=2,
             arrowcolor='#FF851B',
             ax=0, ay=-30),
        
        dict(x='2011-08-05', y=df['SP500'].max() * 0.9,
             text='US Credit Rating Downgrade',
             showarrow=True, arrowhead=2,
             arrowsize=1, arrowwidth=2,
             arrowcolor='#FF4136',
             ax=0, ay=-40),
        
        dict(x='2020-03-23', y=df['SP500'].max() * 0.7,
             text='COVID-19 Market Bottom',
             showarrow=True, arrowhead=2,
             arrowsize=1, arrowwidth=2,
             arrowcolor='#85144b',
             ax=0, ay=-40),
        
        dict(x='2022-01-03', y=df['SP500'].max() * 0.95,
             text='Fed Rate Hikes Begin',
             showarrow=True, arrowhead=2,
             arrowsize=1, arrowwidth=2,
             arrowcolor='#FFDC00',
             ax=0, ay=-30)
    ]

    # Update layout with enhanced styling
    fig.update_layout(
        title={
            'text': 'S&P 500 Index vs VIX:(1990-2024)',
            'y':0.95,
            'x':0.5,
            'xanchor': 'center',
            'yanchor': 'top',
            'font': dict(size=24, color='#444444')
        },
        plot_bgcolor='rgba(240,242,245,0.8)',
        paper_bgcolor='white',
        annotations=market_events,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01,
            bgcolor='rgba(255, 255, 255, 0.8)',
            bordercolor='#444444',
            borderwidth=1
        ),
        hovermode='x unified'
    )

    # Update axes with enhanced styling
    fig.update_xaxes(
        title_text="Date",
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.2)',
        zeroline=False,
        showline=True,
        linewidth=2,
        linecolor='#444444'
    )

    # Update y-axes
    fig.update_yaxes(
        title_text="S&P 500 Index Value",
        type="log",
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.2)',
        zeroline=False,
        showline=True,
        linewidth=2,
        linecolor='#444444',
        secondary_y=False
    )
    
    fig.update_yaxes(
        title_text="VIX Value",
        showgrid=False,
        zeroline=False,
        showline=True,
        linewidth=2,
        linecolor='#444444',
        secondary_y=True,
        range=[0, max(df['VIX']) * 1.1]  # Adjust VIX scale
    )

    return fig

def add_analysis_visualization(df):
    """Add technical analysis with real data"""
    # Calculate moving averages
    df['VIX_MA20'] = df['VIX'].rolling(window=20).mean()
    df['VIX_MA50'] = df['VIX'].rolling(window=50).mean()
    
    # Calculate volatility regimes
    vix_mean = df['VIX'].mean()
    vix_std = df['VIX'].std()
    
    df['Volatility_Regime'] = 'Normal'
    df.loc[df['VIX'] > vix_mean + vix_std, 'Volatility_Regime'] = 'High'
    df.loc[df['VIX'] > vix_mean + 2*vix_std, 'Volatility_Regime'] = 'Extreme'
    df.loc[df['VIX'] < vix_mean - vix_std, 'Volatility_Regime'] = 'Low'
    
    fig = make_subplots(rows=2, cols=1, 
                       shared_xaxes=True,
                       vertical_spacing=0.1,
                       subplot_titles=('S&P 500 vs VIX with Moving Averages', 
                                     'Volatility Regimes'))

    # Upper plot: S&P 500 and VIX with MAs
    fig.add_trace(
        go.Scatter(x=df['Date'], y=df['SP500'],
                  name="S&P 500", line=dict(color='#4299e1', width=2)),
        row=1, col=1
    )
    
    fig.add_trace(
        go.Scatter(x=df['Date'], y=df['VIX'],
                  name="VIX", line=dict(color='#fc8181', width=1)),
        row=1, col=1, secondary_y=True
    )
    
    fig.add_trace(
        go.Scatter(x=df['Date'], y=df['VIX_MA20'],
                  name="VIX 20-day MA", 
                  line=dict(color='#9f7aea', width=1, dash='dash')),
        row=1, col=1, secondary_y=True
    )
    
    fig.add_trace(
        go.Scatter(x=df['Date'], y=df['VIX_MA50'],
                  name="VIX 50-day MA",
                  line=dict(color='#667eea', width=1, dash='dash')),
        row=1, col=1, secondary_y=True
    )
    
    # Lower plot: Volatility regimes
    colors = {'Low': '#2ECC40', 'Normal': '#7FDBFF', 
              'High': '#FF851B', 'Extreme': '#FF4136'}
    
    for regime in colors.keys():
        regime_data = df[df['Volatility_Regime'] == regime]
        fig.add_trace(
            go.Scatter(x=regime_data['Date'], y=regime_data['VIX'],
                      name=f"{regime} Volatility",
                      mode='markers',
                      marker=dict(color=colors[regime], size=6)),
            row=2, col=1
        )

    fig.update_layout(
        height=1000,
        title_text="Market Analysis: S&P 500, VIX, and Volatility Regimes",
        showlegend=True,
        plot_bgcolor='rgba(240,242,245,0.8)',
        paper_bgcolor='white'
    )

    return fig

# Load the real data
print("Loading data...")
df = load_data()

# Create basic visualization
print("\nCreating basic visualization...")
fig1 = create_enhanced_visualization(df)
fig1.show()

# Create analysis visualization
print("\nCreating analysis visualization...")
fig2 = add_analysis_visualization(df)
fig2.show()

Loading data...
Data range: 1990-02-01 00:00:00 to 2023-09-01 00:00:00
Total data points: 236

Creating basic visualization...



Creating analysis visualization...


ValueError: 
Subplot with type '{subplot_type}' at grid position ({row}, {col}) was not
created with the secondary_y spec property set to True. See the docstring
for the specs argument to plotly.subplots.make_subplots for more information.


In [2]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load data
sp500_url = "https://raw.githubusercontent.com/datasets/s-and-p-500/master/data/data.csv"
vix_url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"

# Load and prepare data
sp500_df = pd.read_csv(sp500_url)
vix_df = pd.read_csv(vix_url)

# Convert dates
sp500_df['Date'] = pd.to_datetime(sp500_df['Date'])
vix_df['DATE'] = pd.to_datetime(vix_df['DATE'])

# Rename VIX columns for consistency
vix_df = vix_df.rename(columns={'DATE': 'Date', 'CLOSE': 'VIX'})

# Merge datasets
merged_df = pd.merge(sp500_df[['Date', 'SP500']], 
                    vix_df[['Date', 'VIX']], 
                    on='Date', 
                    how='outer')

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(
        x=sp500_df['Date'],
        y=sp500_df['SP500'],
        name="S&P 500",
        line=dict(color='#1f77b4', width=1.5)
    ),
    secondary_y=False
)

fig.add_trace(
    go.Scatter(
        x=vix_df['Date'],
        y=vix_df['VIX'],
        name="VIX",
        line=dict(color='#ff7f0e', width=1.5)
    ),
    secondary_y=True
)

# Key market events to highlight
events = [
    {'date': '2008-09-15', 'text': '2008 Financial Crisis', 'y_sp500': 1200},
    {'date': '2020-03-23', 'text': '2020 COVID-19 Crisis', 'y_sp500': 2300}
]

# Add annotations for key events
annotations = []
for event in events:
    annotations.append(
        dict(
            x=event['date'],
            y=event['y_sp500'],
            text=event['text'],
            showarrow=True,
            arrowhead=1,
            ax=0,
            ay=-40,
            font=dict(size=12),
            bgcolor='rgba(255, 255, 255, 0.8)'
        )
    )

# Update layout
fig.update_layout(
    title=None,  # Remove title for cleaner look
    plot_bgcolor='white',
    paper_bgcolor='white',
    annotations=annotations,
    showlegend=True,
    legend=dict(
        yanchor="top",
        y=0.99,
        xanchor="left",
        x=0.01,
        bgcolor='rgba(255, 255, 255, 0.8)'
    ),
    margin=dict(l=60, r=60, t=30, b=50)
)

# Update axes
fig.update_xaxes(
    showgrid=False,
    zeroline=False,
    linecolor='black',
    linewidth=1,
    ticks='outside'
)

fig.update_yaxes(
    title_text="S&P 500 Index Value",
    type="log",
    showgrid=False,
    zeroline=False,
    linecolor='black',
    linewidth=1,
    secondary_y=False,
    ticks='outside'
)

fig.update_yaxes(
    title_text="VIX Value",
    showgrid=False,
    zeroline=False,
    linecolor='black',
    linewidth=1,
    secondary_y=True,
    ticks='outside'
)

fig.show()

In [3]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load data
sp500_url = "https://raw.githubusercontent.com/datasets/s-and-p-500/master/data/data.csv"
vix_url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"

# Load and prepare data
sp500_df = pd.read_csv(sp500_url)
vix_df = pd.read_csv(vix_url)

# Convert dates
sp500_df['Date'] = pd.to_datetime(sp500_df['Date'])
vix_df['DATE'] = pd.to_datetime(vix_df['DATE'])

# Rename VIX columns for consistency
vix_df = vix_df.rename(columns={'DATE': 'Date', 'CLOSE': 'VIX'})

# Find common date range
start_date = max(sp500_df['Date'].min(), vix_df['Date'].min())
end_date = min(sp500_df['Date'].max(), vix_df['Date'].max())

# Filter data to common range
sp500_df = sp500_df[(sp500_df['Date'] >= start_date) & (sp500_df['Date'] <= end_date)]
vix_df = vix_df[(vix_df['Date'] >= start_date) & (vix_df['Date'] <= end_date)]

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add S&P 500 trace
fig.add_trace(
    go.Scatter(
        x=sp500_df['Date'],
        y=sp500_df['SP500'],
        name="S&P 500",
        line=dict(color='#4299e1', width=1.5)  # Light blue color
    ),
    secondary_y=False
)

# Add VIX trace
fig.add_trace(
    go.Scatter(
        x=vix_df['Date'],
        y=vix_df['VIX'],
        name="VIX",
        line=dict(color='#fc8181', width=1.5)  # Light red color
    ),
    secondary_y=True
)

# Add annotations for major events
annotations = [
    dict(
        x='2008-09-15',
        y=1200,
        text='2008 Financial Crisis',
        showarrow=True,
        arrowhead=2,
        arrowsize=1,
        arrowwidth=1.5,
        arrowcolor='#666',
        ax=0,
        ay=-40,
        font=dict(size=12),
        bgcolor='rgba(255, 255, 255, 0.8)'
    ),
    dict(
        x='2020-03-23',
        y=2300,
        text='COVID-19 Crisis',
        showarrow=True,
        arrowhead=2,
        arrowsize=1,
        arrowwidth=1.5,
        arrowcolor='#666',
        ax=0,
        ay=-40,
        font=dict(size=12),
        bgcolor='rgba(255, 255, 255, 0.8)'
    )
]

# Update layout with minimal elements
fig.update_layout(
    plot_bgcolor='white',
    paper_bgcolor='white',
    annotations=annotations,
    showlegend=True,
    legend=dict(
        yanchor="top",
        y=0.99,
        xanchor="left",
        x=0.01,
        bgcolor='rgba(255, 255, 255, 0.8)'
    ),
    margin=dict(l=60, r=60, t=30, b=50)
)

# Update axes with minimal gridlines
fig.update_xaxes(
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128, 128, 128, 0.1)',
    zeroline=False,
    showline=True,
    linewidth=1,
    linecolor='rgba(128, 128, 128, 0.5)'
)

# Update y-axes
fig.update_yaxes(
    title_text="S&P 500 Index Value",
    type="log",
    showgrid=True,
    gridwidth=1,
    gridcolor='rgba(128, 128, 128, 0.1)',
    zeroline=False,
    showline=True,
    linewidth=1,
    linecolor='rgba(128, 128, 128, 0.5)',
    secondary_y=False
)

fig.update_yaxes(
    title_text="VIX Value",
    showgrid=False,
    zeroline=False,
    showline=True,
    linewidth=1,
    linecolor='rgba(128, 128, 128, 0.5)',
    secondary_y=True
)

fig.show()

In [5]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from datetime import datetime

# Load and prepare VIX data
def load_vix_data():
    url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"
    df = pd.read_csv(url)
    df['DATE'] = pd.to_datetime(df['DATE'])
    
    # Calculate intraday metrics
    df['IntraDay_Range'] = df['HIGH'] - df['LOW']
    df['Body_Size'] = abs(df['CLOSE'] - df['OPEN'])
    df['Upper_Shadow'] = df['HIGH'] - df[['OPEN', 'CLOSE']].max(axis=1)
    df['Lower_Shadow'] = df[['OPEN', 'CLOSE']].min(axis=1) - df['LOW']
    df['Body_Direction'] = np.where(df['CLOSE'] >= df['OPEN'], 1, -1)
    
    # Calculate moving averages
    df['MA20'] = df['CLOSE'].rolling(window=20).mean()
    
    # Calculate volatility of volatility (VIX of VIX)
    df['VIX_Volatility'] = df['CLOSE'].rolling(window=20).std()
    
    return df

def create_ohlc_visualization(df):
    # Create figure with secondary y-axis
    fig = make_subplots(
        rows=3, 
        cols=1,
        shared_xaxes=True,
        vertical_spacing=0.05,
        row_heights=[0.6, 0.2, 0.2],
        subplot_titles=('VIX Candlestick Pattern', 'Intraday Range', 'Volatility of VIX')
    )

    # Add candlestick chart
    fig.add_trace(
        go.Candlestick(
            x=df['DATE'],
            open=df['OPEN'],
            high=df['HIGH'],
            low=df['LOW'],
            close=df['CLOSE'],
            increasing_line_color='#26A69A',
            decreasing_line_color='#EF5350',
            name='OHLC'
        ),
        row=1, col=1
    )

    # Add 20-day moving average
    fig.add_trace(
        go.Scatter(
            x=df['DATE'],
            y=df['MA20'],
            line=dict(color='#9B59B6', width=1),
            name='20-day MA'
        ),
        row=1, col=1
    )

    # Add intraday range
    fig.add_trace(
        go.Bar(
            x=df['DATE'],
            y=df['IntraDay_Range'],
            marker_color='#7986CB',
            opacity=0.7,
            name='Intraday Range'
        ),
        row=2, col=1
    )

    # Add VIX volatility
    fig.add_trace(
        go.Scatter(
            x=df['DATE'],
            y=df['VIX_Volatility'],
            line=dict(color='#E67E22', width=1.5),
            name='VIX Volatility'
        ),
        row=3, col=1
    )

    # Update layout
    fig.update_layout(
        title=dict(
            text='VIX Intraday Pattern Analysis',
            x=0.5,
            y=0.95
        ),
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=1000,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01,
            bgcolor='rgba(255, 255, 255, 0.8)'
        ),
        xaxis_rangeslider_visible=False
    )

    # Update axes
    fig.update_xaxes(
        showgrid=False,
        zeroline=False,
        showline=True,
        linewidth=1,
        linecolor='gray'
    )

    fig.update_yaxes(
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.1)',
        zeroline=False,
        showline=True,
        linewidth=1,
        linecolor='gray'
    )

    return fig

def analyze_patterns(df):
    """Analyze and print key patterns in the data"""
    analysis = {}
    
    # Calculate average intraday range
    analysis['avg_intraday_range'] = df['IntraDay_Range'].mean()
    
    # Calculate average body size
    analysis['avg_body_size'] = df['Body_Size'].mean()
    
    # Calculate percentage of up vs down days
    total_days = len(df)
    up_days = len(df[df['Body_Direction'] == 1])
    analysis['up_day_percentage'] = (up_days / total_days) * 100
    
    # Find days with unusual volatility (>2 std from mean)
    mean_range = df['IntraDay_Range'].mean()
    std_range = df['IntraDay_Range'].std()
    high_vol_days = df[df['IntraDay_Range'] > (mean_range + 2*std_range)]
    analysis['high_volatility_days'] = len(high_vol_days)
    
    return analysis

# Load data and create visualizations
print("Loading and processing data...")
vix_df = load_vix_data()

# Create visualization
print("\nCreating visualization...")
fig = create_ohlc_visualization(vix_df)
fig.show()

# Analyze patterns
print("\nAnalyzing patterns...")
patterns = analyze_patterns(vix_df)

print("\nKey Findings:")
print(f"Average Intraday Range: {patterns['avg_intraday_range']:.2f}")
print(f"Average Body Size: {patterns['avg_body_size']:.2f}")
print(f"Percentage of Up Days: {patterns['up_day_percentage']:.1f}%")
print(f"Number of High Volatility Days: {patterns['high_volatility_days']}")

Loading and processing data...

Creating visualization...



Analyzing patterns...

Key Findings:
Average Intraday Range: 1.58
Average Body Size: 0.83
Percentage of Up Days: 45.8%
Number of High Volatility Days: 248


In [6]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

# Load VIX data
def load_and_prepare_data():
    url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"
    df = pd.read_csv(url)
    df['DATE'] = pd.to_datetime(df['DATE'])
    
    # Identify significant patterns
    df['Body'] = df['CLOSE'] - df['OPEN']
    df['Upper_Shadow'] = df['HIGH'] - df[['OPEN', 'CLOSE']].max(axis=1)
    df['Lower_Shadow'] = df[['OPEN', 'CLOSE']].min(axis=1) - df['LOW']
    
    # Identify large moves (>20% daily range)
    df['Daily_Range_Pct'] = (df['HIGH'] - df['LOW']) / df['LOW'] * 100
    df['Large_Move'] = df['Daily_Range_Pct'] > 20
    
    return df

# Create candlestick visualization
def create_clean_candlestick(df, start_date='2020-01-01', end_date='2024-01-01'):
    # Filter date range
    mask = (df['DATE'] >= start_date) & (df['DATE'] <= end_date)
    df_period = df.loc[mask]
    
    # Create figure
    fig = go.Figure()
    
    # Add candlestick
    fig.add_trace(
        go.Candlestick(
            x=df_period['DATE'],
            open=df_period['OPEN'],
            high=df_period['HIGH'],
            low=df_period['LOW'],
            close=df_period['CLOSE'],
            increasing_line_color='#26A69A',  # Green for up days
            decreasing_line_color='#EF5350',  # Red for down days
            name='VIX'
        )
    )
    
    # Add annotations for significant events
    significant_moves = df_period[df_period['Large_Move']]
    annotations = []
    
    for idx, row in significant_moves.iterrows():
        annotations.append(
            dict(
                x=row['DATE'],
                y=row['HIGH'],
                text='↑',  # Up arrow for significant move
                showarrow=False,
                font=dict(size=14, color='rgba(68, 68, 68, 0.7)')
            )
        )

    # Update layout for clean look
    fig.update_layout(
        plot_bgcolor='white',
        paper_bgcolor='white',
        margin=dict(l=40, r=40, t=40, b=40),
        xaxis=dict(
            showgrid=False,
            zeroline=False,
            rangeslider=dict(visible=False),  # Remove rangeslider
            showline=True,
            linewidth=1,
            linecolor='black'
        ),
        yaxis=dict(
            showgrid=True,
            gridwidth=0.5,
            gridcolor='rgba(128,128,128,0.1)',
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black'
        ),
        annotations=annotations
    )

    return fig

# Load data
df = load_and_prepare_data()

# Create visualization for recent period
fig = create_clean_candlestick(df)
fig.show()

# Print some pattern analysis
print("\nPattern Analysis:")
recent_df = df[df['DATE'] >= '2020-01-01']

# Identify significant patterns
large_moves = recent_df[recent_df['Large_Move']]
print(f"\nNumber of large daily moves (>20% range): {len(large_moves)}")

# Calculate average daily ranges
print(f"Average daily range: {recent_df['Daily_Range_Pct'].mean():.2f}%")

# Identify trend days (close near high/low)
trend_days = recent_df[
    (recent_df['CLOSE'] >= recent_df['HIGH'] * 0.95) |
    (recent_df['CLOSE'] <= recent_df['LOW'] * 1.05)
]
print(f"Strong trend days: {len(trend_days)}")


Pattern Analysis:

Number of large daily moves (>20% range): 111
Average daily range: 10.99%
Strong trend days: 1113


In [7]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

# Load and prepare VIX data
def load_and_prepare_data():
    url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"
    df = pd.read_csv(url)
    df['DATE'] = pd.to_datetime(df['DATE'])
    
    # Calculate daily range percentage
    df['Daily_Range_Pct'] = (df['HIGH'] - df['LOW']) / df['LOW'] * 100
    
    return df

# Find most volatile period
def find_volatile_period(df, window_size=20):
    df['Avg_Range'] = df['Daily_Range_Pct'].rolling(window=window_size).mean()
    most_volatile_start = df['Avg_Range'].idxmax() - window_size//2
    return df.index[most_volatile_start]

# Create focused candlestick visualization
def create_focused_candlestick(df, start_idx, days=20):
    # Select focused period
    df_period = df.iloc[start_idx:start_idx + days].copy()
    
    # Create figure
    fig = go.Figure()
    
    # Add candlestick
    fig.add_trace(
        go.Candlestick(
            x=df_period['DATE'],
            open=df_period['OPEN'],
            high=df_period['HIGH'],
            low=df_period['LOW'],
            close=df_period['CLOSE'],
            increasing_line_color='#4CAF50',  # Green
            decreasing_line_color='#FF5252',  # Red
            increasing_fillcolor='#4CAF50',   # Solid fill for up days
            decreasing_fillcolor='#FF5252',   # Solid fill for down days
            line=dict(width=2),              # Thicker lines
            whiskerwidth=0.8,                # Thicker whiskers
        )
    )

    # Update layout for clean look
    fig.update_layout(
        plot_bgcolor='white',
        paper_bgcolor='white',
        margin=dict(l=40, r=40, t=40, b=40),
        width=800,      # Fixed width
        height=500,     # Fixed height
        title=dict(
            text=f'VIX Candlestick Chart ({df_period["DATE"].min().strftime("%Y-%m-%d")} to {df_period["DATE"].max().strftime("%Y-%m-%d")})',
            x=0.5,
            y=0.95
        ),
        xaxis=dict(
            showgrid=False,
            zeroline=False,
            rangeslider=dict(visible=False),
            showline=True,
            linewidth=1,
            linecolor='black',
            tickangle=0,
            dtick=2      # Show every other day for clarity
        ),
        yaxis=dict(
            showgrid=True,
            gridwidth=0.5,
            gridcolor='rgba(128,128,128,0.1)',
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black',
            side='right'  # Move y-axis to right side like in reference
        )
    )

    return fig

# Load data
df = load_and_prepare_data()

# Find volatile period (or use March 2020 COVID crash period)
covid_crash_start = df[df['DATE'] >= '2020-03-01'].index[0]
march_2020_idx = covid_crash_start

# Create visualization
fig = create_focused_candlestick(df, march_2020_idx, days=20)
fig.show()

# Print analysis for this period
period_data = df.iloc[march_2020_idx:march_2020_idx + 20]
print("\nPattern Analysis for Selected Period:")
print(f"Date Range: {period_data['DATE'].min().strftime('%Y-%m-%d')} to {period_data['DATE'].max().strftime('%Y-%m-%d')}")
print(f"Highest VIX: {period_data['HIGH'].max():.2f}")
print(f"Average Daily Range: {period_data['Daily_Range_Pct'].mean():.2f}%")
print(f"Number of Up Days: {len(period_data[period_data['CLOSE'] > period_data['OPEN']])}")
print(f"Number of Down Days: {len(period_data[period_data['CLOSE'] < period_data['OPEN']])}")

# Identify significant patterns
largest_range_day = period_data.loc[period_data['Daily_Range_Pct'].idxmax()]
print(f"\nLargest Range Day: {largest_range_day['DATE'].strftime('%Y-%m-%d')}")
print(f"Range: {largest_range_day['Daily_Range_Pct']:.2f}%")


Pattern Analysis for Selected Period:
Date Range: 2020-03-02 to 2020-03-27
Highest VIX: 85.47
Average Daily Range: 30.75%
Number of Up Days: 11
Number of Down Days: 9

Largest Range Day: 2020-03-24
Range: 70.75%


In [8]:
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import numpy as np
from datetime import datetime

# Load S&P 500 companies data with sector information
def load_sector_data():
    # Load S&P 500 companies data
    sp500_companies_url = "https://raw.githubusercontent.com/datasets/s-and-p-500-companies/master/data/constituents.csv"
    companies = pd.read_csv(sp500_companies_url)
    
    # Get unique sectors
    sectors = companies['Sector'].unique()
    
    # Create sector performance data (sample data - replace with actual sector ETF data)
    dates = pd.date_range(start='2020-01-01', end='2024-01-01', freq='D')
    sector_data = pd.DataFrame(index=dates)
    
    # Simulate sector prices with realistic correlations
    np.random.seed(42)
    base_returns = np.random.normal(0, 1, len(dates))
    
    for sector in sectors:
        # Add some randomness to create different but correlated returns
        sector_specific = np.random.normal(0, 0.5, len(dates))
        sector_returns = 0.7 * base_returns + 0.3 * sector_specific
        sector_data[sector] = (1 + sector_returns * 0.01).cumprod() * 100
    
    return sector_data

def create_correlation_matrix(df):
    """Create a correlation matrix heatmap"""
    # Calculate correlation matrix
    corr_matrix = df.pct_change().corr()
    
    # Create heatmap
    fig = go.Figure(data=go.Heatmap(
        z=corr_matrix.values,
        x=corr_matrix.columns,
        y=corr_matrix.columns,
        colorscale='RdBu',
        zmin=-1,
        zmax=1,
        text=np.round(corr_matrix.values, 2),
        texttemplate='%{text}',
        textfont={"size": 10},
        hoverongaps=False
    ))
    
    # Update layout
    fig.update_layout(
        title='Sector Correlation Matrix',
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=800,
        width=800,
        title_x=0.5,
        xaxis=dict(
            tickangle=45,
            side='bottom'
        ),
        yaxis=dict(
            tickangle=0
        )
    )
    
    return fig

def create_sector_performance(df):
    """Create sector performance comparison"""
    # Normalize all sectors to 100 at the start
    normalized_df = df.div(df.iloc[0]) * 100
    
    # Create figure
    fig = go.Figure()
    
    # Add traces for each sector
    colors = px.colors.qualitative.Set3
    for i, sector in enumerate(normalized_df.columns):
        fig.add_trace(
            go.Scatter(
                x=normalized_df.index,
                y=normalized_df[sector],
                name=sector,
                line=dict(color=colors[i % len(colors)], width=2),
                hovertemplate=
                '<b>%{x}</b><br>' +
                f'{sector}: %{{y:.1f}}<br>'
            )
        )
    
    # Add major events annotations
    events = [
        dict(x='2020-03-23', y=70, text='COVID-19 Bottom'),
        dict(x='2021-01-01', y=130, text='Recovery Peak'),
        dict(x='2022-01-01', y=110, text='Rate Hikes Begin')
    ]
    
    # Update layout
    fig.update_layout(
        title='Sector Performance Comparison (Normalized to 100)',
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=600,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01,
            bgcolor='rgba(255, 255, 255, 0.8)'
        ),
        annotations=events,
        hovermode='x unified',
        xaxis=dict(
            showgrid=False,
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black'
        ),
        yaxis=dict(
            showgrid=True,
            gridwidth=1,
            gridcolor='rgba(128,128,128,0.1)',
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black',
            title='Normalized Price'
        )
    )
    
    return fig

def analyze_sector_leadership(df):
    """Analyze sector leadership and create visualization"""
    # Calculate monthly returns
    monthly_returns = df.resample('M').last().pct_change()
    
    # Find monthly leaders and laggards
    leaders = monthly_returns.idxmax(axis=1)
    laggards = monthly_returns.idxmin(axis=1)
    
    # Create figure
    fig = go.Figure()
    
    # Add leader trace
    fig.add_trace(
        go.Scatter(
            x=leaders.index,
            y=[1]*len(leaders),
            mode='markers+text',
            name='Leaders',
            text=leaders.values,
            textposition='top center',
            marker=dict(size=10, color='green', symbol='triangle-up'),
            hovertemplate='Date: %{x}<br>Leader: %{text}<br>'
        )
    )
    
    # Add laggard trace
    fig.add_trace(
        go.Scatter(
            x=laggards.index,
            y=[0]*len(laggards),
            mode='markers+text',
            name='Laggards',
            text=laggards.values,
            textposition='bottom center',
            marker=dict(size=10, color='red', symbol='triangle-down'),
            hovertemplate='Date: %{x}<br>Laggard: %{text}<br>'
        )
    )
    
    # Update layout
    fig.update_layout(
        title='Monthly Sector Leaders and Laggards',
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=400,
        showlegend=True,
        yaxis=dict(
            showticklabels=False,
            showgrid=False,
            zeroline=False
        ),
        xaxis=dict(
            showgrid=False,
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black'
        )
    )
    
    return fig

# Load data
print("Loading sector data...")
sector_data = load_sector_data()

# Create visualizations
print("\nCreating correlation matrix...")
corr_fig = create_correlation_matrix(sector_data)
corr_fig.show()

print("\nCreating performance comparison...")
perf_fig = create_sector_performance(sector_data)
perf_fig.show()

print("\nAnalyzing sector leadership...")
lead_fig = analyze_sector_leadership(sector_data)
lead_fig.show()

# Print additional analysis
print("\nSector Analysis Summary:")
recent_returns = sector_data.iloc[-1] / sector_data.iloc[-30] - 1
print("\nLast Month Performance:")
for sector in recent_returns.sort_values(ascending=False).index:
    print(f"{sector}: {recent_returns[sector]:.1%}")

Loading sector data...


KeyError: 'Sector'

In [9]:
import pandas as pd
import plotly.graph_objects as go
import plotly.express as px
from plotly.subplots import make_subplots
import numpy as np
from datetime import datetime

# Define sector ETFs
SECTOR_ETFS = {
    'Technology': 'XLK',
    'Healthcare': 'XLV',
    'Financials': 'XLF',
    'Consumer Discretionary': 'XLY',
    'Consumer Staples': 'XLP',
    'Energy': 'XLE',
    'Materials': 'XLB',
    'Industrials': 'XLI',
    'Utilities': 'XLU',
    'Real Estate': 'XLRE'
}

# Create sample data (since we can't directly download in this environment)
def create_sample_sector_data():
    dates = pd.date_range(start='2020-01-01', end='2024-01-01', freq='D')
    data = pd.DataFrame(index=dates)
    
    # Create correlated but distinct sector movements
    np.random.seed(42)
    base_market = np.random.normal(0, 1, len(dates))
    
    for sector in SECTOR_ETFS.keys():
        # Create sector-specific characteristics
        if sector == 'Technology':
            sector_bias = 0.02  # Higher growth
        elif sector == 'Utilities':
            sector_bias = 0.01  # More stable
        elif sector == 'Energy':
            sector_bias = 0.03  # More volatile
        else:
            sector_bias = 0.015
            
        # Generate sector prices
        sector_specific = np.random.normal(0, 0.5, len(dates))
        sector_returns = 0.7 * base_market + 0.3 * sector_specific + sector_bias
        data[sector] = (1 + sector_returns * 0.01).cumprod() * 100
        
        # Add COVID-19 impact (March 2020)
        covid_impact = (dates >= '2020-03-01') & (dates <= '2020-03-23')
        data.loc[covid_impact, sector] *= 0.7
        
        # Add recovery
        recovery = (dates >= '2020-03-24') & (dates <= '2020-06-01')
        data.loc[recovery, sector] *= 1.5
    
    return data

def create_correlation_matrix(df):
    """Create a correlation matrix heatmap"""
    # Calculate correlation matrix
    corr_matrix = df.pct_change().corr()
    
    # Create heatmap
    fig = go.Figure(data=go.Heatmap(
        z=corr_matrix.values,
        x=corr_matrix.columns,
        y=corr_matrix.columns,
        colorscale='RdBu',
        zmin=-1,
        zmax=1,
        text=np.round(corr_matrix.values, 2),
        texttemplate='%{text}',
        textfont={"size": 10},
        hoverongaps=False
    ))
    
    # Update layout
    fig.update_layout(
        title='Sector Correlation Matrix',
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=800,
        width=800,
        title_x=0.5,
        xaxis=dict(
            tickangle=45,
            side='bottom'
        ),
        yaxis=dict(
            tickangle=0
        )
    )
    
    return fig

def create_sector_performance(df):
    """Create sector performance comparison"""
    # Normalize all sectors to 100 at the start
    normalized_df = df.div(df.iloc[0]) * 100
    
    # Create figure
    fig = go.Figure()
    
    # Add traces for each sector
    colors = px.colors.qualitative.Set3
    for i, sector in enumerate(normalized_df.columns):
        fig.add_trace(
            go.Scatter(
                x=normalized_df.index,
                y=normalized_df[sector],
                name=sector,
                line=dict(color=colors[i % len(colors)], width=2),
                hovertemplate=
                '<b>%{x}</b><br>' +
                f'{sector}: %{{y:.1f}}<br>'
            )
        )
    
    # Add major market events
    events = [
        dict(
            x='2020-03-23',
            y=60,
            text='COVID-19<br>Bottom',
            showarrow=True,
            arrowhead=1,
            ax=0,
            ay=40
        ),
        dict(
            x='2021-01-04',
            y=140,
            text='Recovery<br>Peak',
            showarrow=True,
            arrowhead=1,
            ax=0,
            ay=-40
        ),
        dict(
            x='2022-01-03',
            y=120,
            text='Rate Hikes<br>Begin',
            showarrow=True,
            arrowhead=1,
            ax=0,
            ay=-40
        )
    ]
    
    # Update layout
    fig.update_layout(
        title='Sector Performance Comparison (Normalized to 100)',
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=600,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01,
            bgcolor='rgba(255, 255, 255, 0.8)'
        ),
        annotations=events,
        hovermode='x unified',
        xaxis=dict(
            showgrid=False,
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black'
        ),
        yaxis=dict(
            showgrid=True,
            gridwidth=1,
            gridcolor='rgba(128,128,128,0.1)',
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black',
            title='Normalized Price'
        )
    )
    
    return fig

def analyze_sector_rotation(df):
    """Create sector rotation analysis visualization"""
    # Calculate monthly returns
    monthly_returns = df.resample('M').last().pct_change()
    
    # Get top and bottom performers
    best_sectors = monthly_returns.idxmax(axis=1)
    worst_sectors = monthly_returns.idxmin(axis=1)
    
    # Create figure
    fig = go.Figure()
    
    # Add best performers
    fig.add_trace(
        go.Scatter(
            x=best_sectors.index,
            y=[1]*len(best_sectors),
            mode='markers+text',
            name='Leaders',
            text=best_sectors.values,
            textposition='top center',
            marker=dict(size=12, color='#2ECC40', symbol='triangle-up'),
            textfont=dict(size=10)
        )
    )
    
    # Add worst performers
    fig.add_trace(
        go.Scatter(
            x=worst_sectors.index,
            y=[0]*len(worst_sectors),
            mode='markers+text',
            name='Laggards',
            text=worst_sectors.values,
            textposition='bottom center',
            marker=dict(size=12, color='#FF4136', symbol='triangle-down'),
            textfont=dict(size=10)
        )
    )
    
    # Update layout
    fig.update_layout(
        title='Monthly Sector Rotation Analysis',
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=500,
        showlegend=True,
        yaxis=dict(
            showticklabels=False,
            showgrid=False,
            zeroline=False
        ),
        xaxis=dict(
            showgrid=False,
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black'
        )
    )
    
    return fig

# Create and display visualizations
print("Creating sample sector data...")
sector_data = create_sample_sector_data()

print("\nGenerating correlation matrix...")
corr_fig = create_correlation_matrix(sector_data)
corr_fig.show()

print("\nGenerating performance comparison...")
perf_fig = create_sector_performance(sector_data)
perf_fig.show()

print("\nAnalyzing sector rotation...")
rotation_fig = analyze_sector_rotation(sector_data)
rotation_fig.show()

# Print summary statistics
print("\nSector Performance Summary (Last 30 Days):")
recent_returns = sector_data.iloc[-1] / sector_data.iloc[-30] - 1
for sector, ret in recent_returns.sort_values(ascending=False).items():
    print(f"{sector}: {ret:.1%}")

Creating sample sector data...

Generating correlation matrix...



Generating performance comparison...



Analyzing sector rotation...



Sector Performance Summary (Last 30 Days):
Technology: 8.1%
Utilities: 8.1%
Consumer Staples: 7.9%
Industrials: 7.8%
Healthcare: 6.9%
Energy: 6.9%
Real Estate: 6.6%
Consumer Discretionary: 6.5%
Materials: 6.2%
Financials: 6.1%


In [15]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np
from datetime import datetime

# Create sample data for three sectors
def create_focused_sector_data():
    dates = pd.date_range(start='2020-01-01', end='2024-01-01', freq='D')
    data = pd.DataFrame(index=dates)
    
    # Create correlated but distinct sector movements
    np.random.seed(42)
    base_market = np.random.normal(0, 1, len(dates))
    
    sectors = {
        'Technology': {'bias': 0.02, 'volatility': 0.5, 'color': '#36A2EB'},  # Blue
        'Energy': {'bias': 0.03, 'volatility': 0.7, 'color': '#FFB631'},      # Orange
        'Real Estate': {'bias': 0.015, 'volatility': 0.4, 'color': '#A78BFA'} # Purple
    }
    
    for sector, params in sectors.items():
        sector_specific = np.random.normal(0, params['volatility'], len(dates))
        sector_returns = 0.7 * base_market + 0.3 * sector_specific + params['bias']
        data[sector] = (1 + sector_returns * 0.01).cumprod() * 100
        
        # Add COVID-19 impact (March 2020)
        covid_impact = (dates >= '2020-03-01') & (dates <= '2020-03-23')
        data.loc[covid_impact, sector] *= 0.7
        
        # Add recovery
        recovery = (dates >= '2020-03-24') & (dates <= '2020-06-01')
        data.loc[recovery, sector] *= 1.5
        
        # Add rate hikes impact (2022)
        rate_hikes = (dates >= '2022-01-03')
        if sector == 'Real Estate':
            data.loc[rate_hikes, sector] *= 0.95
        elif sector == 'Energy':
            data.loc[rate_hikes, sector] *= 1.1
    
    return data

def create_sector_performance(df):
    # Normalize all sectors to 100 at the start
    normalized_df = df.div(df.iloc[0]) * 100
    
    # Create figure
    fig = go.Figure()
    
    # Color scheme
    colors = {
        'Technology': '#36A2EB',
        'Energy': '#FFB631',
        'Real Estate': '#A78BFA'
    }
    
    # Add traces for each sector
    for sector in normalized_df.columns:
        fig.add_trace(
            go.Scatter(
                x=normalized_df.index,
                y=normalized_df[sector],
                name=sector,
                line=dict(color=colors[sector], width=2),
                hovertemplate=
                '<b>%{x}</b><br>' +
                f'{sector}: %{{y:.1f}}<br>'
            )
        )
    
    # Add major market events
    annotations = [
        dict(
            x='2020-03-23',
            y=60,
            text='COVID-19<br>Bottom',
            showarrow=True,
            arrowhead=1,
            ax=0,
            ay=-40,
            font=dict(size=12),
            bgcolor='rgba(255, 255, 255, 0.8)'
        ),
        dict(
            x='2021-01-04',
            y=120,
            text='Recovery<br>Peak',
            showarrow=True,
            arrowhead=1,
            ax=0,
            ay=-40,
            font=dict(size=12),
            bgcolor='rgba(255, 255, 255, 0.8)'
        ),
        dict(
            x='2022-01-03',
            y=110,
            text='Rate Hikes<br>Begin',
            showarrow=True,
            arrowhead=1,
            ax=0,
            ay=-40,
            font=dict(size=12),
            bgcolor='rgba(255, 255, 255, 0.8)'
        )
    ]
    
    # Update layout
    fig.update_layout(
        title=dict(
            text='Sector Performance Comparison (Normalized to 100)',
            x=0.5,
            y=0.95,
            xanchor='center',
            font=dict(size=20)
        ),
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=600,
        width=1000,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.98,
            xanchor="left",
            x=0.01,
            bgcolor='rgba(255, 255, 255, 0.8)',
            font=dict(size=14)
        ),
        annotations=annotations,
        hovermode='x unified',
        xaxis=dict(
            showgrid=True,
            gridwidth=1,
            gridcolor='rgba(128,128,128,0.1)',
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black',
            title='',
            tickfont=dict(size=12)
        ),
        yaxis=dict(
            showgrid=True,
            gridwidth=1,
            gridcolor='rgba(128,128,128,0.1)',
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black',
            title='Normalized Price',
            title_font=dict(size=14),
            tickfont=dict(size=12),
            range=[50, 220]  # Fixed y-axis range for better visualization
        ),
        margin=dict(l=60, r=40, t=80, b=40)
    )
    
    return fig

# Create and display visualization
print("Creating sector data...")
sector_data = create_focused_sector_data()

print("\nGenerating performance comparison...")
fig = create_sector_performance(sector_data)
fig.show()

Creating sector data...

Generating performance comparison...


In [11]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from datetime import datetime

def load_vix_data():
    """Load and prepare VIX data"""
    url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"
    df = pd.read_csv(url)
    df['DATE'] = pd.to_datetime(df['DATE'])
    
    # Calculate additional metrics
    df['Price_Change'] = df['CLOSE'] - df['OPEN']
    df['Daily_Return'] = df['Price_Change'] / df['OPEN'] * 100
    
    # Calculate volume Z-score for unusual volume detection
    df['Volume_MA20'] = df['VOLUME'].rolling(window=20).mean()
    df['Volume_STD20'] = df['VOLUME'].rolling(window=20).std()
    df['Volume_Z_Score'] = (df['VOLUME'] - df['Volume_MA20']) / df['Volume_STD20']
    
    return df

def create_volume_price_analysis(df):
    # Create figure with secondary y-axis
    fig = make_subplots(
        rows=3, 
        cols=1,
        row_heights=[0.5, 0.25, 0.25],
        shared_xaxes=True,
        vertical_spacing=0.05,
        subplot_titles=(
            'Price and Volume Analysis',
            'Volume Profile',
            'Volume Anomaly Detection'
        )
    )

    # 1. Main Price Chart with Volume Bars
    fig.add_trace(
        go.Candlestick(
            x=df['DATE'],
            open=df['OPEN'],
            high=df['HIGH'],
            low=df['LOW'],
            close=df['CLOSE'],
            name='OHLC',
            increasing_line_color='#26A69A',
            decreasing_line_color='#EF5350'
        ),
        row=1, col=1
    )

    # Add volume bars with color based on price direction
    colors = ['#26A69A' if close >= open else '#EF5350' 
             for close, open in zip(df['CLOSE'], df['OPEN'])]
    
    fig.add_trace(
        go.Bar(
            x=df['DATE'],
            y=df['VOLUME'],
            name='Volume',
            marker_color=colors,
            opacity=0.5
        ),
        row=2, col=1
    )

    # 2. Volume Z-Score for Anomaly Detection
    fig.add_trace(
        go.Scatter(
            x=df['DATE'],
            y=df['Volume_Z_Score'],
            name='Volume Z-Score',
            line=dict(color='#9B59B6', width=1.5)
        ),
        row=3, col=1
    )

    # Add threshold lines for unusual volume
    fig.add_hline(
        y=2, 
        line_dash="dash", 
        line_color="red",
        opacity=0.5,
        row=3, col=1,
        annotation_text="High Volume Threshold"
    )
    
    fig.add_hline(
        y=-2,
        line_dash="dash",
        line_color="red",
        opacity=0.5,
        row=3, col=1,
        annotation_text="Low Volume Threshold"
    )

    # Update layout
    fig.update_layout(
        title={
            'text': 'VIX Price-Volume Relationship Analysis',
            'y':0.95,
            'x':0.5,
            'xanchor': 'center',
            'yanchor': 'top',
            'font': dict(size=20)
        },
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=1200,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01,
            bgcolor='rgba(255, 255, 255, 0.8)'
        ),
        xaxis_rangeslider_visible=False
    )

    # Update y-axes
    fig.update_yaxes(
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.2)',
        zeroline=False,
        showline=True,
        linewidth=1,
        linecolor='rgba(128,128,128,0.5)'
    )

    # Update x-axes
    fig.update_xaxes(
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.2)',
        zeroline=False,
        showline=True,
        linewidth=1,
        linecolor='rgba(128,128,128,0.5)'
    )

    return fig

def analyze_volume_patterns(df):
    """Analyze and identify significant volume patterns"""
    analysis = {
        'high_volume_days': len(df[df['Volume_Z_Score'] > 2]),
        'low_volume_days': len(df[df['Volume_Z_Score'] < -2]),
        'avg_up_volume': df[df['Daily_Return'] > 0]['VOLUME'].mean(),
        'avg_down_volume': df[df['Daily_Return'] < 0]['VOLUME'].mean(),
    }
    return analysis

def identify_volume_clusters(df):
    """Identify and analyze volume clusters"""
    # Calculate volume-weighted average price (VWAP)
    df['VWAP'] = (df['HIGH'] + df['LOW'] + df['CLOSE']) / 3
    df['Volume_Price_Level'] = df['VWAP'] * df['VOLUME']
    
    # Create volume profile
    price_levels = pd.qcut(df['CLOSE'], q=10)
    volume_profile = df.groupby(price_levels)['VOLUME'].sum()
    
    return volume_profile

# Load and prepare data
print("Loading and preparing data...")
df = load_vix_data()

# Create visualization
print("\nCreating visualization...")
fig = create_volume_price_analysis(df)
fig.show()

# Analyze patterns
print("\nAnalyzing volume patterns...")
patterns = analyze_volume_patterns(df)
print("\nVolume Pattern Analysis:")
print(f"High Volume Days (Z-score > 2): {patterns['high_volume_days']}")
print(f"Low Volume Days (Z-score < -2): {patterns['low_volume_days']}")
print(f"Average Up-Day Volume: {patterns['avg_up_volume']:,.0f}")
print(f"Average Down-Day Volume: {patterns['avg_down_volume']:,.0f}")

# Analyze volume clusters
print("\nAnalyzing volume clusters...")
volume_profile = identify_volume_clusters(df)
print("\nVolume Profile by Price Level:")
print(volume_profile)

Loading and preparing data...


KeyError: 'VOLUME'

In [12]:
import pandas as pd
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from datetime import datetime

def load_and_prepare_data():
    """Load and prepare VIX data"""
    url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"
    df = pd.read_csv(url)
    df['DATE'] = pd.to_datetime(df['DATE'])
    
    # Calculate additional metrics
    df['Daily_Range'] = df['HIGH'] - df['LOW']
    df['Body_Size'] = abs(df['CLOSE'] - df['OPEN'])
    df['Price_Change'] = df['CLOSE'] - df['OPEN']
    df['Daily_Return'] = df['Price_Change'] / df['OPEN'] * 100
    
    # Calculate Z-scores for trading ranges
    df['Range_MA20'] = df['Daily_Range'].rolling(window=20).mean()
    df['Range_STD20'] = df['Daily_Range'].rolling(window=20).std()
    df['Range_Z_Score'] = (df['Daily_Range'] - df['Range_MA20']) / df['Range_STD20']
    
    return df

def create_price_range_analysis(df, start_date='2020-01-01'):
    # Filter for recent data
    df = df[df['DATE'] >= start_date].copy()
    
    # Create figure with secondary y-axis
    fig = make_subplots(
        rows=3, 
        cols=1,
        row_heights=[0.5, 0.25, 0.25],
        shared_xaxes=True,
        vertical_spacing=0.05,
        subplot_titles=(
            'VIX Price Action',
            'Daily Trading Range',
            'Range Volatility (Z-Score)'
        )
    )

    # 1. Main Price Chart
    fig.add_trace(
        go.Candlestick(
            x=df['DATE'],
            open=df['OPEN'],
            high=df['HIGH'],
            low=df['LOW'],
            close=df['CLOSE'],
            name='OHLC',
            increasing_line_color='#26A69A',
            decreasing_line_color='#EF5350'
        ),
        row=1, col=1
    )

    # 2. Daily Trading Range
    colors = ['#26A69A' if close >= open else '#EF5350' 
             for close, open in zip(df['CLOSE'], df['OPEN'])]
    
    fig.add_trace(
        go.Bar(
            x=df['DATE'],
            y=df['Daily_Range'],
            name='Daily Range',
            marker_color=colors,
            opacity=0.7
        ),
        row=2, col=1
    )

    # Add 20-day moving average of range
    fig.add_trace(
        go.Scatter(
            x=df['DATE'],
            y=df['Range_MA20'],
            name='20-day Avg Range',
            line=dict(color='#9B59B6', width=1.5)
        ),
        row=2, col=1
    )

    # 3. Range Z-Score
    fig.add_trace(
        go.Scatter(
            x=df['DATE'],
            y=df['Range_Z_Score'],
            name='Range Z-Score',
            line=dict(color='#3498DB', width=1.5)
        ),
        row=3, col=1
    )

    # Add threshold lines for unusual ranges
    fig.add_hline(
        y=2, 
        line_dash="dash", 
        line_color="red",
        opacity=0.5,
        row=3, col=1,
        annotation_text="High Volatility"
    )
    
    fig.add_hline(
        y=-2,
        line_dash="dash",
        line_color="red",
        opacity=0.5,
        row=3, col=1,
        annotation_text="Low Volatility"
    )

    # Update layout
    fig.update_layout(
        title={
            'text': 'VIX Price Range Analysis',
            'y':0.95,
            'x':0.5,
            'xanchor': 'center',
            'yanchor': 'top',
            'font': dict(size=20)
        },
        plot_bgcolor='white',
        paper_bgcolor='white',
        height=1200,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01,
            bgcolor='rgba(255, 255, 255, 0.8)'
        ),
        xaxis_rangeslider_visible=False
    )

    # Update y-axes
    fig.update_yaxes(
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.2)',
        zeroline=False,
        showline=True,
        linewidth=1,
        linecolor='rgba(128,128,128,0.5)'
    )

    # Update x-axes
    fig.update_xaxes(
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.2)',
        zeroline=False,
        showline=True,
        linewidth=1,
        linecolor='rgba(128,128,128,0.5)'
    )

    return fig

def analyze_price_patterns(df):
    """Analyze and identify significant price patterns"""
    analysis = {
        'high_range_days': len(df[df['Range_Z_Score'] > 2]),
        'low_range_days': len(df[df['Range_Z_Score'] < -2]),
        'avg_up_range': df[df['Daily_Return'] > 0]['Daily_Range'].mean(),
        'avg_down_range': df[df['Daily_Return'] < 0]['Daily_Range'].mean(),
        'largest_range_day': df.loc[df['Daily_Range'].idxmax(), 'DATE'].strftime('%Y-%m-%d')
    }
    return analysis

# Load and prepare data
print("Loading and preparing data...")
df = load_and_prepare_data()

# Create visualization
print("\nCreating visualization...")
fig = create_price_range_analysis(df)
fig.show()

# Analyze patterns
print("\nAnalyzing price patterns...")
patterns = analyze_price_patterns(df)
print("\nPrice Pattern Analysis:")
print(f"High Range Days (Z-score > 2): {patterns['high_range_days']}")
print(f"Low Range Days (Z-score < -2): {patterns['low_range_days']}")
print(f"Average Up-Day Range: {patterns['avg_up_range']:.2f}")
print(f"Average Down-Day Range: {patterns['avg_down_range']:.2f}")
print(f"Largest Range Day: {patterns['largest_range_day']}")

Loading and preparing data...

Creating visualization...



Analyzing price patterns...

Price Pattern Analysis:
High Range Days (Z-score > 2): 500
Low Range Days (Z-score < -2): 5
Average Up-Day Range: 1.85
Average Down-Day Range: 1.56
Largest Range Day: 2008-10-10


In [13]:
import React, { useState } from 'react';
import {
  ComposedChart,
  Line,
  Area,
  XAxis,
  YAxis,
  CartesianGrid,
  Tooltip,
  Legend,
  ResponsiveContainer,
} from 'recharts';
import { Card, CardContent, CardHeader, CardTitle } from "@/components/ui/card";

const Dashboard = () => {
  // Sample data - normally you'd fetch and process this
  const data = [
    {
      Date: "2000-01-01",
      SP500: 1394.46,
      CPI: 168.8,
      LongInterestRate: 6.66,
      RealPrice: 2789.68,
      Event: "Dot-com Peak"
    },
    {
      Date: "2008-09-15",
      SP500: 1192.70,
      CPI: 215.5,
      LongInterestRate: 4.69,
      RealPrice: 1990.45,
      Event: "Lehman Brothers Collapse"
    },
    {
      Date: "2020-03-23",
      SP500: 2237.40,
      CPI: 258.1,
      LongInterestRate: 1.55,
      RealPrice: 3120.34,
      Event: "COVID-19 Market Bottom"
    }
  ];

  const CustomTooltip = ({ active, payload, label }) => {
    if (active && payload && payload.length) {
      return (
        <div className="bg-white p-4 border rounded shadow-lg">
          <p className="font-bold">{`Date: ${label}`}</p>
          {payload.map((entry, index) => (
            <p key={index} style={{ color: entry.color }}>
              {`${entry.name}: ${entry.value.toFixed(2)}`}
            </p>
          ))}
          {data.find(item => item.Date === label)?.Event && (
            <p className="text-red-500 font-bold mt-2">
              Event: {data.find(item => item.Date === label).Event}
            </p>
          )}
        </div>
      );
    }
    return null;
  };

  return (
    <div className="space-y-4">
      <Card className="w-full">
        <CardHeader>
          <CardTitle>S&P 500 Historical Performance with Macroeconomic Indicators</CardTitle>
        </CardHeader>
        <CardContent>
          <div className="h-96">
            <ResponsiveContainer width="100%" height="100%">
              <ComposedChart data={data}>
                <CartesianGrid strokeDasharray="3 3" />
                <XAxis 
                  dataKey="Date" 
                  tick={{ fontSize: 12 }}
                />
                <YAxis 
                  yAxisId="left"
                  tick={{ fontSize: 12 }}
                  label={{ value: 'S&P 500 & CPI', angle: -90, position: 'insideLeft' }}
                />
                <YAxis 
                  yAxisId="right" 
                  orientation="right"
                  tick={{ fontSize: 12 }}
                  label={{ value: 'Interest Rate (%)', angle: 90, position: 'insideRight' }}
                />
                <Tooltip content={<CustomTooltip />} />
                <Legend />
                
                {/* S&P 500 Line */}
                <Line
                  yAxisId="left"
                  type="monotone"
                  dataKey="SP500"
                  stroke="#8884d8"
                  strokeWidth={2}
                  dot={false}
                  name="S&P 500"
                />
                
                {/* CPI Area */}
                <Area
                  yAxisId="left"
                  type="monotone"
                  dataKey="CPI"
                  fill="#82ca9d"
                  stroke="#82ca9d"
                  fillOpacity={0.3}
                  name="CPI"
                />
                
                {/* Interest Rate Line */}
                <Line
                  yAxisId="right"
                  type="monotone"
                  dataKey="LongInterestRate"
                  stroke="#ff7300"
                  strokeWidth={2}
                  dot={false}
                  name="Interest Rate"
                />
              </ComposedChart>
            </ResponsiveContainer>
          </div>
        </CardContent>
      </Card>
    </div>
  );
};

export default Dashboard;

SyntaxError: invalid syntax (4005455995.py, line 1)

In [14]:
import pandas as pd
import plotly.graph_objects as go
import numpy as np

# Load and prepare VIX data
def load_and_prepare_data():
    url = "https://raw.githubusercontent.com/datasets/finance-vix/master/data/vix-daily.csv"
    df = pd.read_csv(url)
    df['DATE'] = pd.to_datetime(df['DATE'])
    
    # Calculate daily range percentage
    df['Daily_Range_Pct'] = (df['HIGH'] - df['LOW']) / df['LOW'] * 100
    
    return df

def create_focused_candlestick(df, start_idx, days=20):
    # Select focused period
    df_period = df.iloc[start_idx:start_idx + days].copy()
    
    # Create figure
    fig = go.Figure()
    
    # Add candlestick
    fig.add_trace(
        go.Candlestick(
            x=df_period['DATE'],
            open=df_period['OPEN'],
            high=df_period['HIGH'],
            low=df_period['LOW'],
            close=df_period['CLOSE'],
            increasing_line_color='#4CAF50',  # Green
            decreasing_line_color='#FF5252',  # Red
            increasing_fillcolor='#4CAF50',   # Solid fill for up days
            decreasing_fillcolor='#FF5252',   # Solid fill for down days
            name='VIX',  # Add name for legend
            line=dict(width=2),
            whiskerwidth=0.8,
        )
    )
    
    # Update layout for improved visualization
    fig.update_layout(
        plot_bgcolor='white',
        paper_bgcolor='white',
        margin=dict(l=40, r=40, t=60, b=40),
        width=800,
        height=500,
        title=dict(
            text='VIX Index During COVID-19 Market Crash',
            x=0.5,
            y=0.95,
            font=dict(size=20)
        ),
        xaxis=dict(
            title='Date',
            showgrid=True,
            gridwidth=0.5,
            gridcolor='rgba(128,128,128,0.1)',
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black',
            tickangle=45,  # Angle the dates for better readability
            dtick='D2'     # Show every other day
        ),
        yaxis=dict(
            title='VIX Index Value',
            showgrid=True,
            gridwidth=0.5,
            gridcolor='rgba(128,128,128,0.1)',
            zeroline=False,
            showline=True,
            linewidth=1,
            linecolor='black',
            side='right'
        ),
        showlegend=True,  # Show legend
        legend=dict(
            x=0.85,
            y=0.95,
            bgcolor='rgba(255,255,255,0.8)',
            bordercolor='black',
            borderwidth=1
        ),
        annotations=[
            dict(
                text=f"Period: {df_period['DATE'].min().strftime('%Y-%m-%d')} to {df_period['DATE'].max().strftime('%Y-%m-%d')}",
                showarrow=False,
                x=0.5,
                y=1.08,
                xref='paper',
                yref='paper',
                font=dict(size=12)
            )
        ]
    )
    
    return fig

# Load data
df = load_and_prepare_data()

# Find March 2020 COVID crash period
covid_crash_start = df[df['DATE'] >= '2020-03-01'].index[0]
march_2020_idx = covid_crash_start

# Create visualization
fig = create_focused_candlestick(df, march_2020_idx, days=20)
fig.show()

# Print analysis for this period
period_data = df.iloc[march_2020_idx:march_2020_idx + 20]
print("\nPattern Analysis for Selected Period:")
print(f"Date Range: {period_data['DATE'].min().strftime('%Y-%m-%d')} to {period_data['DATE'].max().strftime('%Y-%m-%d')}")
print(f"Highest VIX: {period_data['HIGH'].max():.2f}")
print(f"Average Daily Range: {period_data['Daily_Range_Pct'].mean():.2f}%")
print(f"Number of Up Days: {len(period_data[period_data['CLOSE'] > period_data['OPEN']])}")
print(f"Number of Down Days: {len(period_data[period_data['CLOSE'] < period_data['OPEN']])}")

# Identify significant patterns
largest_range_day = period_data.loc[period_data['Daily_Range_Pct'].idxmax()]
print(f"\nLargest Range Day: {largest_range_day['DATE'].strftime('%Y-%m-%d')}")
print(f"Range: {largest_range_day['Daily_Range_Pct']:.2f}%")


Pattern Analysis for Selected Period:
Date Range: 2020-03-02 to 2020-03-27
Highest VIX: 85.47
Average Daily Range: 30.75%
Number of Up Days: 11
Number of Down Days: 9

Largest Range Day: 2020-03-24
Range: 70.75%


In [19]:
def create_enhanced_visualization(df):
    # Create figure with secondary y-axis
    fig = make_subplots(specs=[[{"secondary_y": True}]])
    
    # Add S&P 500 trace with log scale
    fig.add_trace(
        go.Scatter(
            x=df['Date'],
            y=df['SP500'],
            name="S&P 500",
            line=dict(color='#4299e1', width=2)
        ),
        secondary_y=False
    )

    # Add VIX trace
    fig.add_trace(
        go.Scatter(
            x=df['Date'],
            y=df['VIX'],
            name="VIX",
            line=dict(color='#fc8181', width=2)
        ),
        secondary_y=True
    )

    # Define crisis periods to highlight
    crisis_annotations = [
        # 2008 Financial Crisis
        dict(
            x0='2008-09-01', x1='2009-03-31',
            y0=0, y1=1,
            fillcolor='rgba(255, 0, 0, 0.1)',
            line_width=0,
            layer='below',
            name='2008 Crisis'
        ),
        # 2020 COVID Crisis
        dict(
            x0='2020-02-19', x1='2020-04-07',
            y0=0, y1=1,
            fillcolor='rgba(255, 0, 0, 0.1)',
            line_width=0,
            layer='below',
            name='COVID-19 Crisis'
        )
    ]

    # Add the shaded regions for crises
    for shape in crisis_annotations:
        fig.add_shape(
            type='rect',
            xref='x',
            yref='paper',
            **shape
        )

    # Define annotations including crisis labels
    annotations = [
        dict(x='2008-09-15', y=df['SP500'].max(), 
             text='2008 Financial Crisis<br>Lehman Brothers Bankruptcy',
             showarrow=True, arrowhead=2,
             arrowsize=1, arrowwidth=2,
             arrowcolor='#FF4136',
             ax=0, ay=-40),
        
        dict(x='2020-03-23', y=df['SP500'].max() * 0.7,
             text='COVID-19 Market Bottom',
             showarrow=True, arrowhead=2,
             arrowsize=1, arrowwidth=2,
             arrowcolor='#85144b',
             ax=0, ay=-40)
    ]

    # Update layout with enhanced styling
    fig.update_layout(
        title={
            'text': 'S&P 500 Index vs VIX with Crisis Periods Highlighted',
            'y':0.95,
            'x':0.5,
            'xanchor': 'center',
            'yanchor': 'top',
            'font': dict(size=24, color='#444444')
        },
        plot_bgcolor='rgba(240,242,245,0.8)',
        paper_bgcolor='white',
        annotations=annotations,
        showlegend=True,
        legend=dict(
            yanchor="top",
            y=0.99,
            xanchor="left",
            x=0.01,
            bgcolor='rgba(255, 255, 255, 0.8)',
            bordercolor='#444444',
            borderwidth=1
        ),
        hovermode='x unified'
    )

    # Update axes styling
    fig.update_xaxes(
        title_text="Date",
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.2)',
        zeroline=False,
        showline=True,
        linewidth=2,
        linecolor='#444444'
    )

    fig.update_yaxes(
        title_text="S&P 500 Index Value",
        type="log",
        showgrid=True,
        gridwidth=1,
        gridcolor='rgba(128,128,128,0.2)',
        zeroline=False,
        showline=True,
        linewidth=2,
        linecolor='#444444',
        secondary_y=False
    )
    
    fig.update_yaxes(
        title_text="VIX Value",
        showgrid=False,
        zeroline=False,
        showline=True,
        linewidth=2,
        linecolor='#444444',
        secondary_y=True,
        range=[0, max(df['VIX']) * 1.1]
    )

    return fig
fig.show()